In [9]:
import MetaTrader5 as mt5
from datetime import datetime, timedelta, time

from __init__ import Backtester, get_ohlc_history, create_ohlc_fig, evaluate_backtest

In [10]:
symbol = 'DE40'
start_dt = datetime(2023, 1, 1)
end_dt = datetime.now()

# get historical data
mt5.initialize()
ohlc = get_ohlc_history(symbol, mt5.TIMEFRAME_H1, start_dt, end_dt)

# prepare data set
ohlc['day'] = ohlc['time'].dt.dayofweek
ohlc['time_hms'] = ohlc['time'].dt.time
ohlc['hour'] = ohlc['time'].dt.hour

ohlc['high_20'] = ohlc['high'].rolling(24*5).max().shift(1)
ohlc['low_20'] = ohlc['low'].rolling(24*5).min().shift(1)

ohlc['range'] = ohlc['high'] - ohlc['low']

ohlc = ohlc.dropna()
print(ohlc)

def get_entry_signal(x):
    if x['close'] > x['high_20']:
        return 'buy'
    
    elif x['close'] < x['low_20']:
        return 'sell'
    
def get_exit_signal(x):
    if x['close'] > x['high_20']:
        return 'buy'
    
    elif x['close'] < x['low_20']:
        return 'sell'

ohlc['signal'] = ohlc.apply(get_entry_signal, axis=1)
ohlc['exit_signal'] = ohlc.apply(get_exit_signal, axis=1)

ohlc_fig = create_ohlc_fig(ohlc)
ohlc_fig

                    time      open      high       low     close  day  \
120  2023-01-09 09:00:00  14694.55  14699.65  14662.55  14669.55    0   
121  2023-01-09 10:00:00  14674.45  14677.95  14624.85  14637.65    0   
122  2023-01-09 11:00:00  14638.65  14657.65  14632.15  14637.65    0   
123  2023-01-09 12:00:00  14638.25  14674.15  14632.25  14671.15    0   
124  2023-01-09 13:00:00  14671.25  14690.65  14657.65  14678.65    0   
...                  ...       ...       ...       ...       ...  ...   
9343 2024-08-09 18:00:00  17700.72  17727.03  17690.69  17692.18    4   
9344 2024-08-09 19:00:00  17692.18  17712.15  17676.28  17708.69    4   
9345 2024-08-09 20:00:00  17708.69  17775.95  17705.70  17738.14    4   
9346 2024-08-09 21:00:00  17738.64  17752.64  17721.72  17744.69    4   
9347 2024-08-09 22:00:00  17745.18  17782.60  17738.71  17776.13    4   

      time_hms  hour   high_20    low_20  range  
120   09:00:00     9  14714.65  13840.75  37.10  
121   10:00:00    10  1

In [11]:
# create signal function
def on_bar(data, trades, orders):
    
    open_trades = trades[trades['state'] == 'open']
    num_open_trades = open_trades.shape[0]
    
    # entry signal
    if data['signal'] == 'buy' and not num_open_trades:
        orders.open_trade('DE40', 1, 'buy')
    
    elif data['signal'] == 'sell' and not num_open_trades:
        orders.open_trade('DE40', 1, 'sell')
        
    # exit signal
    if num_open_trades:
        trade = open_trades.iloc[0]

        if trade['order_type'] == 'buy' and data['exit_signal'] == 'sell':
            orders.close_trade(trade)
        elif trade['order_type'] == 'sell' and data['exit_signal'] == 'buy':
            orders.close_trade(trade)


In [12]:
# backtest parameters
starting_balance = 10000
currency = 'EUR'
exchange_rate = 1
commission = -1

# backtest
bt = Backtester()
bt.set_starting_balance(starting_balance, currency=currency)
bt.set_exchange_rate(exchange_rate)
bt.set_commission(commission)

bt.set_historical_data(ohlc)
bt.set_on_bar(on_bar)

bt.run_backtest()

bt.trades

state symbol order_type volume            open_time open_price  \
0   closed   DE40        buy      1  2023-01-09 14:00:00   14678.15   
1   closed   DE40       sell      1  2023-01-19 14:00:00   14947.85   
2   closed   DE40        buy      1  2023-02-01 21:00:00   15179.25   
3   closed   DE40        buy      1  2023-03-03 16:00:00   15522.75   
4   closed   DE40       sell      1  2023-03-10 20:00:00   15339.35   
5   closed   DE40        buy      1  2023-03-29 16:00:00   15284.52   
6   closed   DE40       sell      1  2023-05-25 10:00:00   15871.36   
7   closed   DE40        buy      1  2023-06-12 23:00:00   16140.23   
8   closed   DE40       sell      1  2023-06-21 15:00:00    16086.4   
9   closed   DE40        buy      1  2023-06-30 11:00:00   16024.15   
10  closed   DE40       sell      1  2023-07-06 06:00:00   15898.89   
11  closed   DE40        buy      1  2023-07-13 10:00:00   16025.07   
12  closed   DE40        buy      1  2023-07-27 11:00:00   16206.61   
13  closed   DE40       sell      1  2023-08-03 09:00:00   15987.01   
14  closed   DE40       sell      1  2023-08-17 03:00:00   15708.02   
15  closed   DE40        buy      1  2023-08-24 10:00:00   15822.01   
16  closed   DE40       sell      1  2023-09-05 10:00:00   15757.21   
17  closed   DE40        buy      1  2023-09-15 06:00:00   15893.29   
18  closed   DE40       sell      1  2023-09-21 21:00:00   15561.47   
19  closed   DE40        buy      1  2023-10-10 11:00:00   15350.07   
20  closed   DE40       sell      1  2023-10-18 19:00:00   15081.93   
21  closed   DE40        buy      1  2023-11-01 23:00:00    14978.7   
22  closed   DE40       sell      1  2023-12-18 17:00:00   16651.87   
23  closed   DE40       sell      1  2024-01-03 11:00:00   16747.39   
24  closed   DE40        buy      1  2024-01-11 08:00:00   16785.35   
25  closed   DE40       sell      1  2024-01-17 07:00:00   16481.48   
26  closed   DE40        buy      1  2024-01-24 09:00:00   16728.45   
27  closed   DE40       sell      1  2024-02-13 21:00:00   16839.11   
28  closed   DE40        buy      1  2024-02-15 21:00:00   17084.17   
29  closed   DE40       sell      1  2024-04-04 22:00:00    18212.9   
30  closed   DE40        buy      1  2024-04-23 13:00:00    18000.0   
31  closed   DE40       sell      1  2024-05-23 21:00:00   18604.94   
32  closed   DE40        buy      1  2024-05-28 09:00:00   18792.49   
33  closed   DE40       sell      1  2024-05-29 23:00:00   18492.18   
34  closed   DE40       sell      1  2024-06-11 14:00:00   18389.92   
35  closed   DE40        buy      1  2024-06-26 10:00:00   18273.74   
36  closed   DE40       sell      1  2024-07-18 21:00:00   18336.01   
37  closed   DE40        buy      1  2024-07-31 21:00:00   18514.83   
38  closed   DE40       sell      1  2024-08-01 18:00:00   18090.92   

             close_time close_price sl tp   profit commission profit_net  \
0   2023-01-19 13:00:00    14999.35  0  0   321.20         -1      320.2   
1   2023-01-26 07:00:00    15165.35  0  0  -217.50         -1     -218.5   
2   2023-02-10 14:00:00    15276.75  0  0    97.50         -1       96.5   
3   2023-03-10 10:00:00    15396.25  0  0  -126.50         -1     -127.5   
4   2023-03-22 13:00:00    15257.95  0  0    81.40         -1       80.4   
5   2023-05-24 16:00:00    15869.28  0  0   584.76         -1     583.76   
6   2023-06-12 22:00:00    16121.42  0  0  -250.06         -1    -251.06   
7   2023-06-20 11:00:00    16157.02  0  0    16.79         -1      15.79   
8   2023-06-30 10:00:00    15990.27  0  0    96.13         -1      95.13   
9   2023-07-06 03:00:00     15891.0  0  0  -133.15         -1    -134.15   
10  2023-07-12 17:00:00     15991.7  0  0   -92.81         -1     -93.81   
11  2023-07-26 15:00:00    16071.01  0  0    45.94         -1      44.94   
12  2023-08-02 11:00:00    16023.18  0  0  -183.43         -1    -184.43   
13  2023-08-10 16:00:00    15951.64  0  0    35.37         -1      34.37   
14  2023-08-24 08:00:00 

In [13]:
pnl_chart = bt.plot_pnl()
pnl_chart

In [14]:
backtest_fig = bt.visualize_backtest(ohlc, indicators=['high_20', 'low_20'])
backtest_fig

In [15]:
evaluate_backtest(bt.trades)

biggest_profit 1711.49
biggest_loss -290.01


state symbol order_type volume           open_time open_price  \
0   closed   DE40        buy      1 2023-01-09 14:00:00   14678.15   
2   closed   DE40        buy      1 2023-02-01 21:00:00   15179.25   
4   closed   DE40       sell      1 2023-03-10 20:00:00   15339.35   
5   closed   DE40        buy      1 2023-03-29 16:00:00   15284.52   
7   closed   DE40        buy      1 2023-06-12 23:00:00   16140.23   
8   closed   DE40       sell      1 2023-06-21 15:00:00    16086.4   
11  closed   DE40        buy      1 2023-07-13 10:00:00   16025.07   
13  closed   DE40       sell      1 2023-08-03 09:00:00   15987.01   
18  closed   DE40       sell      1 2023-09-21 21:00:00   15561.47   
20  closed   DE40       sell      1 2023-10-18 19:00:00   15081.93   
21  closed   DE40        buy      1 2023-11-01 23:00:00    14978.7   
26  closed   DE40        buy      1 2024-01-24 09:00:00   16728.45   
28  closed   DE40        buy      1 2024-02-15 21:00:00   17084.17   
29  closed   DE40       sell      1 2024-04-04 22:00:00    18212.9   
30  closed   DE40        buy      1 2024-04-23 13:00:00    18000.0   
34  closed   DE40       sell      1 2024-06-11 14:00:00   18389.92   
35  closed   DE40        buy      1 2024-06-26 10:00:00   18273.74   
38  closed   DE40       sell      1 2024-08-01 18:00:00   18090.92   

            close_time close_price sl tp   profit commission profit_net  \
0  2023-01-19 13:00:00    14999.35  0  0   321.20         -1      320.2   
2  2023-02-10 14:00:00    15276.75  0  0    97.50         -1       96.5   
4  2023-03-22 13:00:00    15257.95  0  0    81.40         -1       80.4   
5  2023-05-24 16:00:00    15869.28  0  0   584.76         -1     583.76   
7  2023-06-20 11:00:00    16157.02  0  0    16.79         -1      15.79   
8  2023-06-30 10:00:00    15990.27  0  0    96.13         -1      95.13   
11 2023-07-26 15:00:00    16071.01  0  0    45.94         -1      44.94   
13 2023-08-10 16:00:00    15951.64  0  0    35.37         -1      34.37   
18 2023-10-10 10:00:00    15253.54  0  0   307.93         -1     306.93   
20 2023-11-01 22:00:00    14937.83  0  0   144.10         -1      143.1   
21 2023-12-18 16:00:00    16690.19  0  0  1711.49         -1    1710.49   
26 2024-02-13 16:00:00    16873.19  0  0   144.74         -1     143.74   
28 2024-04-04 21:00:00    18376.57  0  0  1292.40         -1     1291.4   
29 2024-04-23 09:00:00    17961.12  0  0   251.78         -1     250.78   
30 2024-05-22 21:00:00    18635.48  0  0   635.48         -1     634.48   
34 2024-06-24 16:00:00    18260.14  0  0   129.78         -1     128.78   
35 2024-07-18 18:00:00    18402.51  0  0   128.77         -1     127.77   
38 2024-08-09 22:00:00    17776.13  0  0   314.79         -1     313.79   

   profit_cumulative  
0              320.2  
2              198.2  
4              151.1  
5             734.86  
7             499.59  
8             594.72  
11             411.7  
13            261.64  
18               0.5  
20            -71.86  
21           1638.63  
26           1148.01  
28           2279.67  
29           2530.45  
30           3164.93  
34           2672.59  
35           2800.36  
38           2648.18

state symbol order_type volume           open_time open_price  \
1   closed   DE40       sell      1 2023-01-19 14:00:00   14947.85   
3   closed   DE40        buy      1 2023-03-03 16:00:00   15522.75   
6   closed   DE40       sell      1 2023-05-25 10:00:00   15871.36   
9   closed   DE40        buy      1 2023-06-30 11:00:00   16024.15   
10  closed   DE40       sell      1 2023-07-06 06:00:00   15898.89   
12  closed   DE40        buy      1 2023-07-27 11:00:00   16206.61   
14  closed   DE40       sell      1 2023-08-17 03:00:00   15708.02   
15  closed   DE40        buy      1 2023-08-24 10:00:00   15822.01   
16  closed   DE40       sell      1 2023-09-05 10:00:00   15757.21   
17  closed   DE40        buy      1 2023-09-15 06:00:00   15893.29   
19  closed   DE40        buy      1 2023-10-10 11:00:00   15350.07   
22  closed   DE40       sell      1 2023-12-18 17:00:00   16651.87   
23  closed   DE40       sell      1 2024-01-03 11:00:00   16747.39   
24  closed   DE40        buy      1 2024-01-11 08:00:00   16785.35   
25  closed   DE40       sell      1 2024-01-17 07:00:00   16481.48   
27  closed   DE40       sell      1 2024-02-13 21:00:00   16839.11   
31  closed   DE40       sell      1 2024-05-23 21:00:00   18604.94   
32  closed   DE40        buy      1 2024-05-28 09:00:00   18792.49   
33  closed   DE40       sell      1 2024-05-29 23:00:00   18492.18   
36  closed   DE40       sell      1 2024-07-18 21:00:00   18336.01   
37  closed   DE40        buy      1 2024-07-31 21:00:00   18514.83   

            close_time close_price sl tp  profit commission profit_net  \
1  2023-01-26 07:00:00    15165.35  0  0 -217.50         -1     -218.5   
3  2023-03-10 10:00:00    15396.25  0  0 -126.50         -1     -127.5   
6  2023-06-12 22:00:00    16121.42  0  0 -250.06         -1    -251.06   
9  2023-07-06 03:00:00     15891.0  0  0 -133.15         -1    -134.15   
10 2023-07-12 17:00:00     15991.7  0  0  -92.81         -1     -93.81   
12 2023-08-02 11:00:00    16023.18  0  0 -183.43         -1    -184.43   
14 2023-08-24 08:00:00    15823.49  0  0 -115.47         -1    -116.47   
15 2023-09-05 09:00:00    15780.62  0  0  -41.39         -1     -42.39   
16 2023-09-15 05:00:00    15874.41  0  0 -117.20         -1     -118.2   
17 2023-09-21 15:00:00    15603.28  0  0 -290.01         -1    -291.01   
19 2023-10-18 16:00:00    15135.61  0  0 -214.46         -1    -215.46   
22 2024-01-02 10:00:00     16799.1  0  0 -147.23         -1    -148.23   
23 2024-01-11 05:00:00    16765.75  0  0  -18.36         -1     -19.36   
24 2024-01-16 10:00:00    16540.73  0  0 -244.62         -1    -245.62   
25 2024-01-23 09:00:00    16701.63  0  0 -220.15         -1    -221.15   
27 2024-02-15 10:00:00    16997.85  0  0 -158.74         -1    -159.74   
31 2024-05-28 06:00:00    18789.18  0  0 -184.24         -1    -185.24   
32 2024-05-29 15:00:00    18534.41  0  0 -258.08         -1    -259.08   
33 2024-06-06 10:00:00    18667.98  0  0 -175.80         -1     -176.8   
36 2024-07-23 13:00:00    18584.34  0  0 -248.33         -1    -249.33   
37 2024-08-01 17:00:00    18299.19  0  0 -215.64         -1    -216.64   

   profit_cumulative  
1              101.7  
3               70.7  
6              483.8  
9             460.57  
10            366.76  
12            227.27  
14            145.17  
15            102.78  
16            -15.42  
17           -306.43  
19           -214.96  
22            1490.4  
23           1471.04  
24           1225.42  
25           1004.27  
27            988.27  
31           2979.69  
32           2720.61  
33           2543.81  
36           2551.03  
37           2334.39

avg_win 352.24166666666673
avg_loss -173.9604761904762
count_profit_trades 18
count_loss_trades 21
win_rate 0.86
rrr 2.02


order_type   profit
0        buy  3271.79
1       sell  -584.61

state symbol order_type volume           open_time open_price  \
0   closed   DE40        buy      1 2023-01-09 14:00:00   14678.15   
1   closed   DE40       sell      1 2023-01-19 14:00:00   14947.85   
2   closed   DE40        buy      1 2023-02-01 21:00:00   15179.25   
3   closed   DE40        buy      1 2023-03-03 16:00:00   15522.75   
4   closed   DE40       sell      1 2023-03-10 20:00:00   15339.35   
5   closed   DE40        buy      1 2023-03-29 16:00:00   15284.52   
6   closed   DE40       sell      1 2023-05-25 10:00:00   15871.36   
7   closed   DE40        buy      1 2023-06-12 23:00:00   16140.23   
8   closed   DE40       sell      1 2023-06-21 15:00:00    16086.4   
9   closed   DE40        buy      1 2023-06-30 11:00:00   16024.15   
10  closed   DE40       sell      1 2023-07-06 06:00:00   15898.89   
11  closed   DE40        buy      1 2023-07-13 10:00:00   16025.07   
12  closed   DE40        buy      1 2023-07-27 11:00:00   16206.61   
13  closed   DE40       sell      1 2023-08-03 09:00:00   15987.01   
14  closed   DE40       sell      1 2023-08-17 03:00:00   15708.02   
15  closed   DE40        buy      1 2023-08-24 10:00:00   15822.01   
16  closed   DE40       sell      1 2023-09-05 10:00:00   15757.21   
17  closed   DE40        buy      1 2023-09-15 06:00:00   15893.29   
18  closed   DE40       sell      1 2023-09-21 21:00:00   15561.47   
19  closed   DE40        buy      1 2023-10-10 11:00:00   15350.07   
20  closed   DE40       sell      1 2023-10-18 19:00:00   15081.93   
21  closed   DE40        buy      1 2023-11-01 23:00:00    14978.7   
22  closed   DE40       sell      1 2023-12-18 17:00:00   16651.87   
23  closed   DE40       sell      1 2024-01-03 11:00:00   16747.39   
24  closed   DE40        buy      1 2024-01-11 08:00:00   16785.35   
25  closed   DE40       sell      1 2024-01-17 07:00:00   16481.48   
26  closed   DE40        buy      1 2024-01-24 09:00:00   16728.45   
27  closed   DE40       sell      1 2024-02-13 21:00:00   16839.11   
28  closed   DE40        buy      1 2024-02-15 21:00:00   17084.17   
29  closed   DE40       sell      1 2024-04-04 22:00:00    18212.9   
30  closed   DE40        buy      1 2024-04-23 13:00:00    18000.0   
31  closed   DE40       sell      1 2024-05-23 21:00:00   18604.94   
32  closed   DE40        buy      1 2024-05-28 09:00:00   18792.49   
33  closed   DE40       sell      1 2024-05-29 23:00:00   18492.18   
34  closed   DE40       sell      1 2024-06-11 14:00:00   18389.92   
35  closed   DE40        buy      1 2024-06-26 10:00:00   18273.74   
36  closed   DE40       sell      1 2024-07-18 21:00:00   18336.01   
37  closed   DE40        buy      1 2024-07-31 21:00:00   18514.83   
38  closed   DE40       sell      1 2024-08-01 18:00:00   18090.92   

            close_time close_price sl tp   profit commission profit_net  \
0  2023-01-19 13:00:00    14999.35  0  0   321.20         -1      320.2   
1  2023-01-26 07:00:00    15165.35  0  0  -217.50         -1     -218.5   
2  2023-02-10 14:00:00    15276.75  0  0    97.50         -1       96.5   
3  2023-03-10 10:00:00    15396.25  0  0  -126.50         -1     -127.5   
4  2023-03-22 13:00:00    15257.95  0  0    81.40         -1       80.4   
5  2023-05-24 16:00:00    15869.28  0  0   584.76         -1     583.76   
6  2023-06-12 22:00:00    16121.42  0  0  -250.06         -1    -251.06   
7  2023-06-20 11:00:00    16157.02  0  0    16.79         -1      15.79   
8  2023-06-30 10:00:00    15990.27  0  0    96.13         -1      95.13   
9  2023-07-06 03:00:00     15891.0  0  0  -133.15         -1    -134.15   
10 2023-07-12 17:00:00     15991.7  0  0   -92.81         -1     -93.81   
11 2023-07-26 15:00:00    16071.01  0  0    45.94         -1      44.94   
12 2023-08-02 11:00:00    16023.18  0  0  -183.43         -1    -184.43   
13 2023-08-10 16:00:00    15951.64  0  0    35.37         -1      34.37   
14 2023-08-24 08:00:00    15823.49  0  0  -115.47         -1    -116.47   
15 2

state symbol order_type volume           open_time open_price  \
0   closed   DE40        buy      1 2023-01-09 14:00:00   14678.15   
1   closed   DE40       sell      1 2023-01-19 14:00:00   14947.85   
2   closed   DE40        buy      1 2023-02-01 21:00:00   15179.25   
3   closed   DE40        buy      1 2023-03-03 16:00:00   15522.75   
4   closed   DE40       sell      1 2023-03-10 20:00:00   15339.35   
5   closed   DE40        buy      1 2023-03-29 16:00:00   15284.52   
6   closed   DE40       sell      1 2023-05-25 10:00:00   15871.36   
7   closed   DE40        buy      1 2023-06-12 23:00:00   16140.23   
8   closed   DE40       sell      1 2023-06-21 15:00:00    16086.4   
9   closed   DE40        buy      1 2023-06-30 11:00:00   16024.15   
10  closed   DE40       sell      1 2023-07-06 06:00:00   15898.89   
11  closed   DE40        buy      1 2023-07-13 10:00:00   16025.07   
12  closed   DE40        buy      1 2023-07-27 11:00:00   16206.61   
13  closed   DE40       sell      1 2023-08-03 09:00:00   15987.01   
14  closed   DE40       sell      1 2023-08-17 03:00:00   15708.02   
15  closed   DE40        buy      1 2023-08-24 10:00:00   15822.01   
16  closed   DE40       sell      1 2023-09-05 10:00:00   15757.21   
17  closed   DE40        buy      1 2023-09-15 06:00:00   15893.29   
18  closed   DE40       sell      1 2023-09-21 21:00:00   15561.47   
19  closed   DE40        buy      1 2023-10-10 11:00:00   15350.07   
20  closed   DE40       sell      1 2023-10-18 19:00:00   15081.93   
21  closed   DE40        buy      1 2023-11-01 23:00:00    14978.7   
22  closed   DE40       sell      1 2023-12-18 17:00:00   16651.87   
23  closed   DE40       sell      1 2024-01-03 11:00:00   16747.39   
24  closed   DE40        buy      1 2024-01-11 08:00:00   16785.35   
25  closed   DE40       sell      1 2024-01-17 07:00:00   16481.48   
26  closed   DE40        buy      1 2024-01-24 09:00:00   16728.45   
27  closed   DE40       sell      1 2024-02-13 21:00:00   16839.11   
28  closed   DE40        buy      1 2024-02-15 21:00:00   17084.17   
29  closed   DE40       sell      1 2024-04-04 22:00:00    18212.9   
30  closed   DE40        buy      1 2024-04-23 13:00:00    18000.0   
31  closed   DE40       sell      1 2024-05-23 21:00:00   18604.94   
32  closed   DE40        buy      1 2024-05-28 09:00:00   18792.49   
33  closed   DE40       sell      1 2024-05-29 23:00:00   18492.18   
34  closed   DE40       sell      1 2024-06-11 14:00:00   18389.92   
35  closed   DE40        buy      1 2024-06-26 10:00:00   18273.74   
36  closed   DE40       sell      1 2024-07-18 21:00:00   18336.01   
37  closed   DE40        buy      1 2024-07-31 21:00:00   18514.83   
38  closed   DE40       sell      1 2024-08-01 18:00:00   18090.92   

            close_time close_price sl tp   profit commission profit_net  \
0  2023-01-19 13:00:00    14999.35  0  0   321.20         -1      320.2   
1  2023-01-26 07:00:00    15165.35  0  0  -217.50         -1     -218.5   
2  2023-02-10 14:00:00    15276.75  0  0    97.50         -1       96.5   
3  2023-03-10 10:00:00    15396.25  0  0  -126.50         -1     -127.5   
4  2023-03-22 13:00:00    15257.95  0  0    81.40         -1       80.4   
5  2023-05-24 16:00:00    15869.28  0  0   584.76         -1     583.76   
6  2023-06-12 22:00:00    16121.42  0  0  -250.06         -1    -251.06   
7  2023-06-20 11:00:00    16157.02  0  0    16.79         -1      15.79   
8  2023-06-30 10:00:00    15990.27  0  0    96.13         -1      95.13   
9  2023-07-06 03:00:00     15891.0  0  0  -133.15         -1    -134.15   
10 2023-07-12 17:00:00     15991.7  0  0   -92.81         -1     -93.81   
11 2023-07-26 15:00:00    16071.01  0  0    45.94         -1      44.94   
12 2023-08-02 11:00:00    16023.18  0  0  -183.43         -1    -184.43   
13 2023-08-10 16:00:00    15951.64  0  0    35.37         -1      34.37   
14 2023-08-24 08:00:00    15823.49  0  0  -115.47         -1    -116.47   
15 2

ValueError: Plotly Express cannot process wide-form data with columns of different type.